In [ ]:
import random
import networkx as nx
import matplotlib.pyplot as plt
from matplotlib.patches import Circle
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
import numpy as np
from PIL import Image
from matplotlib.animation import FuncAnimation

In [ ]:
import random

# Define the rooms and their adjacent rooms
room_layout = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"],
    # Include tasks and their corresponding rooms
    "T1": ["Reactor"],
    "T2": ["Medbay"],
    "T3": ["Electrical"],
    "T4": ["Cafeteria"],
    "T5": ["Storage"],
    "T6": ["Admin"],
    "T7": ["Security"],
    "T8": ["Oxygen"],
    "T9": ["Upper Engine"],
    "T10": ["Lower Engine"],
    "T11": ["Reactor"],
    "T12": ["Medbay"],
    "T13": ["Electrical"],
    "T14": ["Cafeteria"],
    "T15": ["Storage"],
    "T16": ["Admin"],
}

rooms = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"]
}

# Initialize the positions of crewmates, imposter, and tasks
crewmates = ['C1', 'C2', 'C3', 'C4']
imposter = 'I'
tasks = ['T1', 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T10',
         'T11', 'T12', 'T13', 'T14', 'T15', 'T16']

# Ensure the number of tasks is less than or equal to the number of crewmates
num_crewmates = len(crewmates)
num_tasks = len(tasks)

# Assign random positions to crewmates, imposter, and tasks
crewmates_positions = dict(zip(crewmates, random.sample(list(rooms.keys()), len(crewmates))))
imposter_position = random.choice(list(rooms.keys()))

# Assign tasks to crewmates ensuring an equal split
tasks_per_crewmate = num_tasks // num_crewmates
tasks_assigned = {crewmate: [] for crewmate in crewmates}

# Assign tasks to roomss
tasks_positions = {task: random.choice(list(room_layout.keys())) for task in tasks}

for _ in range(tasks_per_crewmate):
    for crewmate in crewmates:
        available_tasks = set(tasks) - set(sum(tasks_assigned.values(), []))
        task = random.choice(list(available_tasks))
        tasks_assigned[crewmate].append(task)

        
# Print the corrected initial setup
print("Initial Setup:")
print("Rooms:", list(rooms.keys()))
print("Crewmates Positions:", crewmates_positions)
print("Imposter Position:", imposter_position)
print("Tasks Assigned:", tasks_assigned)
print("Tasks Positions:", tasks_positions)


# Function to handle crewmate movement
def crewmate_move(crewmate):
    current_room = crewmates_positions[crewmate]
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    crewmates_positions[crewmate] = new_room
    print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle imposter movement
def imposter_move():
    global imposter_position
    current_room = imposter_position
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    imposter_position = new_room
    print(f"The imposter moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    current_room = crewmates_positions[crewmate]
    available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

    if available_tasks:
        valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
        if valid_tasks:
            task = random.choice(valid_tasks)
            print(f"{crewmate} is performing task {task} in {current_room}")
            tasks_completed[crewmate].add(task)
        else:
            print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
    else:
        print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a dictionary to track completed tasks for each crewmate
tasks_completed = {crewmate: set() for crewmate in crewmates}
print("tasks completed:", tasks_completed)



def delegate_uncompleted_tasks(killed_crewmate):
    uncompleted_tasks = set(tasks_assigned[killed_crewmate]) - set(tasks_completed[killed_crewmate])
    
    # Shuffle the uncompleted tasks to distribute them randomly
    uncompleted_tasks = list(uncompleted_tasks)
    random.shuffle(uncompleted_tasks)

    tasks_per_crewmate = len(uncompleted_tasks) // (num_crewmates - 1)
    
    # Distribute tasks equally among remaining crewmates
    for i, crewmate in enumerate(crewmates):
        if crewmate != killed_crewmate and crewmate not in crewmates_killed:
            start = i * tasks_per_crewmate
            end = (i + 1) * tasks_per_crewmate if i != num_crewmates - 2 else None
            tasks_assigned[crewmate].extend(uncompleted_tasks[start:end])
            
    
    tasks_assigned[killed_crewmate] = []
    




# Function to check crewmate death
def check_crewmate_death():
    global imposter_position
    for crewmate, position in crewmates_positions.items():
        if position == imposter_position and crewmate not in crewmates_killed:
            print(f"{crewmate} has been killed by the imposter!")
            crewmates_killed.add(crewmate)
            delegate_uncompleted_tasks(crewmate)
            
            # Remove killed crewmate from the list
            crewmates.remove(crewmate)
            
            return True
    return False

def all_crewmates_killed():
    return len(crewmates) == 0

# Function to handle crewmate movement
def crewmate_move(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        adjacent_rooms = rooms[current_room]
        new_room = random.choice(adjacent_rooms)
        crewmates_positions[crewmate] = new_room
        print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a set to track killed crewmates
crewmates_killed = set()


    
def game_ended():
    return all_tasks_completed() or all_crewmates_killed()
    

# Function to check if all tasks are completed
def all_tasks_completed():
    completed_tasks_union = set().union(*tasks_completed.values())
    return completed_tasks_union == set(tasks)

# Function to check if all crewmates are killed
def all_crewmates_killed():
    return len(crewmates_killed) == num_crewmates
    
    
#Game Simulation Loop
while not game_ended(): 
    print("\nCurrent State:")
    print("Crewmates Positions:", crewmates_positions)
    print("Imposter Position:", imposter_position)

    # Crewmates' movement and task assignment
    for crewmate in crewmates:
        crewmate_move(crewmate)
        crewmate_task(crewmate)

    # Imposter's movement
    imposter_move()

    # Check crewmate death
    check_crewmate_death()

    #print("crewmates: ", crewmates)



# Print the final state after the game ends
print("\nFinal State:")
print("Crewmates Positions:", crewmates_positions)
print("Imposter Position:", imposter_position)
print("Tasks Assigned:", tasks_assigned)
print("Tasks Completed:", tasks_completed)
print("Crewmates Killed:", crewmates_killed)

if all_tasks_completed():
    print("\nCrewmates Win! All tasks completed.")
elif all_crewmates_killed():
    print("\nImposter Wins! All crewmates killed.")

In [ ]:
import random
import networkx as nx
import matplotlib.pyplot as plt
from matplotlib.patches import Circle
from matplotlib.offsetbox import OffsetImage, AnnotationBbox
import numpy as np
from PIL import Image


# Define the paths to Among Us character images
character_images = {
    'C1': 'crewmate1.png',
    'C2': 'crewmate2.png',
    'C3': 'crewmate3.png',
    'C4': 'crewmate4.png',
    'I': 'imposter.png'
}

# Define different sizes for each room
room_sizes = {
    'Reactor': 9000,
    'Medbay': 7000,
    'Electrical': 8000,
    'Cafeteria': 6000,
    'Storage': 7000,
    'Admin': 9000,
    'Security': 6000,
    'Oxygen': 6000,
    'Upper Engine': 8000,
    'Lower Engine': 8000
}

tasks = {
    'Admin': ['T16', 'T6'],
    'Cafeteria': ['T14', 'T4'],
    'Medbay': ['T12', 'T2'],
    'Security': ['T7'],
    'Storage': ['T15', 'T5'],
    'Lower Engine': ['T10'],
    'Electrical' : ['T3', 'T13'],
    'Reactor' : ['T11', 'T1'],
    'Oxygen' : ['T8'],
    'Upper Engine' : ['T9'],
    
}


# Create a directed graph
G = nx.DiGraph()

# Add nodes and edges
for room, connections in rooms.items():
    G.add_node(room)
    for connection in connections:
        G.add_edge(room, connection)

pos = nx.spring_layout(G, seed=42, k=0.3, iterations=1000)

plt.figure(figsize=(16, 12))
plt.subplots_adjust(left=0.05, right=0.95, top=0.95, bottom=0.05)

nx.draw_networkx_edges(G, pos, width=1, alpha=0.5, edge_color='gray')

# Plot the rooms as rectangles with darker colored outlines
colors = ['darkred', 'darkgreen', 'darkblue', 'darkorange', 'darkviolet', 'darkcyan', 'darkgrey']
room_colors = {room: colors[i % len(colors)] for i, room in enumerate(G.nodes)}
nx.draw_networkx_nodes(
    G,
    pos,
    node_color='white',
    node_size=[room_sizes[node] for node in G.nodes],
    node_shape='s',
    edgecolors=[room_colors[node] for node in G.nodes],
    linewidths=3,
)

# Add task labels on the top left, and room names next to the rooms
for room, connections in rooms.items():
    tasks_in_room = tasks.get(room, [])  # Get the tasks for the current room
    tasks_text = '\n'.join(tasks_in_room)
    # Display room names next to the rooms
    plt.text(pos[room][0], pos[room][1] - 0.2, room, fontsize=10, ha='center', va='center', fontweight='bold')

     
    
# Plot Among Us characters inside the rooms
for character, room in crewmates_positions.items():
    image_path = character_images.get(character, 'path/to/default_character.png')

    try:
        room_x, room_y = pos[room]
        room_width, room_height = 0.15, 0.15 

        rand_x = np.clip(room_x + np.random.uniform(-room_width / 2, room_width / 2), -1, 1)
        rand_y = np.clip(room_y + np.random.uniform(-room_height / 2, room_height / 2), -1, 1)

        img = Image.open(image_path)
        imagebox = OffsetImage(np.array(img), zoom=0.05)  # Convert PIL Image to numpy array
        ab = AnnotationBbox(imagebox, (rand_x, rand_y), frameon=False, pad=0)
        plt.gca().add_artist(ab)
    except Exception as e:
        print(f"Error loading image for {character}: {e}")

# Plot the imposter inside its initial room
imposter_image_path = character_images.get('I', 'path/to/default_character.png')
try:
    imposter_room_x, imposter_room_y = pos[imposter_position]
    imposter_room_width, imposter_room_height = 0.15, 0.15 

    imposter_rand_x = np.clip(imposter_room_x + np.random.uniform(-imposter_room_width / 2, imposter_room_width / 2), -1, 1)
    imposter_rand_y = np.clip(imposter_room_y + np.random.uniform(-imposter_room_height / 2, imposter_room_height / 2), -1, 1)

    imposter_img = Image.open(imposter_image_path)
    imposter_imagebox = OffsetImage(np.array(imposter_img), zoom=0.05)
    imposter_ab = AnnotationBbox(imposter_imagebox, (imposter_rand_x, imposter_rand_y), frameon=False, pad=0)
    plt.gca().add_artist(imposter_ab)
except Exception as e:
    print(f"Error loading image for imposter: {e}")
    

# Plot small circles representing tasks inside the rooms
task_radius = 0.1 
for room, tasks_in_room in tasks.items():
    for task_index, task in enumerate(tasks_in_room):
        task_x = pos[room][0] + np.random.uniform(-0.1, 0.1)
        task_y = pos[room][1] + np.random.uniform(-0.1, 0.1)
        plt.scatter(task_x, task_y, color='yellow', s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)


    
plt.title('Among Us Map with Tasks')
plt.axis('off')
plt.show()

In [ ]:
# game where tasks are equally delegated

In [ ]:
room_layout = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"],
    # Include tasks and their corresponding rooms
    "T1": ["Reactor"],
    "T2": ["Medbay"],
    "T3": ["Electrical"],
    "T4": ["Cafeteria"],
    "T5": ["Storage"],
    "T6": ["Admin"],
    "T7": ["Security"],
    "T8": ["Oxygen"],
    "T9": ["Upper Engine"],
    "T10": ["Lower Engine"],
    "T11": ["Reactor"],
    "T12": ["Medbay"],
    "T13": ["Electrical"],
    "T14": ["Cafeteria"],
    "T15": ["Storage"],
    "T16": ["Admin"],
}

rooms = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"]
}

# Initialize the positions of crewmates, imposter, and tasks
crewmates = ['C1', 'C2', 'C3', 'C4', 'C5', 'C6']
imposter = 'I'
tasks = ['T1', 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T10',
         'T11', 'T12', 'T13', 'T14', 'T15', 'T16']

# Define different sizes for each room
room_sizes = {
    'Reactor': 9000,
    'Medbay': 7000,
    'Electrical': 8000,
    'Cafeteria': 6000,
    'Storage': 7000,
    'Admin': 9000,
    'Security': 6000,
    'Oxygen': 6000,
    'Upper Engine': 8000,
    'Lower Engine': 8000
}

tasks = {
    'Admin': ['T16', 'T6'],
    'Cafeteria': ['T14', 'T4'],
    'Medbay': ['T12', 'T2'],
    'Security': ['T7'],
    'Storage': ['T15', 'T5'],
    'Lower Engine': ['T10'],
    'Electrical' : ['T3', 'T13'],
    'Reactor' : ['T11', 'T1'],
    'Oxygen' : ['T8'],
    'Upper Engine' : ['T9'],
    
}

character_images = {
    'C1': 'crewmate1.png',
    'C2': 'crewmate2.png',
    'C3': 'crewmate3.png',
    'C4': 'crewmate4.png',
    'C5': 'crewmate5.png',
    'C6': 'crewmate6.png',
    'I': 'imposter.png'
}

# Ensure the number of tasks is less than or equal to the number of crewmates
num_crewmates = len(crewmates)
num_tasks = len(tasks)

# Assign random positions to crewmates, imposter, and tasks
crewmates_positions = dict(zip(crewmates, random.sample(list(rooms.keys()), len(crewmates))))
imposter_position = random.choice(list(rooms.keys()))

# Assign tasks to crewmates ensuring an equal split
tasks_per_crewmate = num_tasks // num_crewmates
tasks_assigned = {crewmate: [] for crewmate in crewmates}

# Assign tasks to rooms without ensuring uniqueness
tasks_positions = {task: random.choice(list(room_layout.keys())) for task in tasks}

for _ in range(tasks_per_crewmate):
    for crewmate in crewmates:
        available_tasks = set(tasks) - set(sum(tasks_assigned.values(), []))
        task = random.choice(list(available_tasks))
        tasks_assigned[crewmate].append(task)

        
# Print the corrected initial setup
print("Initial Setup:")
print("Rooms:", list(rooms.keys()))
print("Crewmates Positions:", crewmates_positions)
print("Imposter Position:", imposter_position)
print("Tasks Assigned:", tasks_assigned)
print("Tasks Positions:", tasks_positions)


# Function to handle crewmate movement
def crewmate_move(crewmate):
    current_room = crewmates_positions[crewmate]
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    crewmates_positions[crewmate] = new_room
    print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle imposter movement
def imposter_move():
    global imposter_position
    current_room = imposter_position
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    imposter_position = new_room
    print(f"The imposter moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
                
                # Remove completed task from the tasks dictionary
                if task in tasks:
                    tasks[current_room].remove(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a dictionary to track completed tasks for each crewmate
tasks_completed = {crewmate: set() for crewmate in crewmates}
print("tasks completed:", tasks_completed)



def delegate_uncompleted_tasks(killed_crewmate):
    uncompleted_tasks = set(tasks_assigned[killed_crewmate]) - set(tasks_completed[killed_crewmate])
    
    # Shuffle the uncompleted tasks to distribute them randomly
    uncompleted_tasks = list(uncompleted_tasks)
    random.shuffle(uncompleted_tasks)

    tasks_per_crewmate = len(uncompleted_tasks) // (num_crewmates - 1)
    
    # Distribute tasks equally among remaining crewmates
    for i, crewmate in enumerate(crewmates):
        if crewmate != killed_crewmate and crewmate not in crewmates_killed:
            start = i * tasks_per_crewmate
            end = (i + 1) * tasks_per_crewmate if i != num_crewmates - 2 else None
            tasks_assigned[crewmate].extend(uncompleted_tasks[start:end])
            
    
    tasks_assigned[killed_crewmate] = []
    




# Function to check crewmate death
def check_crewmate_death():
    global imposter_position
    for crewmate, position in crewmates_positions.items():
        if position == imposter_position and crewmate not in crewmates_killed:
            print(f"{crewmate} has been killed by the imposter!")
            crewmates_killed.add(crewmate)
            delegate_uncompleted_tasks(crewmate)

            # Remove killed crewmate from the list
            crewmates.remove(crewmate)

            # Update the character image for the killed crewmate
            character_images[crewmate] = f'deadcrewmate{crewmate[1]}.png'

            return True
    return False

def all_crewmates_killed():
    return len(crewmates) == 0

# Function to handle crewmate movement
def crewmate_move(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        adjacent_rooms = rooms[current_room]
        new_room = random.choice(adjacent_rooms)
        crewmates_positions[crewmate] = new_room
        print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a set to track killed crewmates
crewmates_killed = set()


    
def game_ended():
    return all_tasks_completed() or all_crewmates_killed()
    

# Function to check if all tasks are completed
def all_tasks_completed():
    completed_tasks_union = set().union(*tasks_completed.values())
    return completed_tasks_union == set(tasks)

# Function to check if all crewmates are killed
def all_crewmates_killed():
    return len(crewmates_killed) == num_crewmates
   

task_positions = {}
for room, tasks_in_room in rooms.items():
    for task_index, task in enumerate(tasks_in_room):
        task_x = pos[room][0] + np.random.uniform(-0.1, 0.1)
        task_y = pos[room][1] + np.random.uniform(-0.1, 0.1)
        task_positions[task] = (task_x, task_y)
    

# Function to update the animation frame
def update(frame):
    plt.clf()

    # Crewmates' movement and task assignment
    for crewmate in crewmates:
        crewmate_move(crewmate)
        crewmate_task(crewmate)
    print(crewmates)

    # Imposter's movement
    imposter_move()

    # Check crewmate death
    if check_crewmate_death():
        if all_crewmates_killed():
            print("All crewmates have been killed. Imposter wins!")
        return

    # Draw edges
    nx.draw_networkx_edges(G, pos, width=1, alpha=0.5, edge_color='gray')

    # Draw nodes
    nx.draw_networkx_nodes(
        G,
        pos,
        node_color='white',
        node_size=[room_sizes[node] for node in G.nodes],
        node_shape='s',
        edgecolors=[room_colors[node] for node in G.nodes],
        linewidths=3,
    )

    # Add task labels on the top left, and room names next to the rooms
    for room, connections in rooms.items():
        tasks_in_room = tasks.get(room, [])  # Get the tasks for the current room
        tasks_text = '\n'.join(tasks_in_room)
        plt.text(pos[room][0], pos[room][1] - 0.2, room, fontsize=10, ha='center', va='center', fontweight='bold')

    # Plot Among Us characters inside the rooms
    for character, room in crewmates_positions.items():
        image_path = character_images.get(character, 'path/to/default_character.png')

        try:
            room_x, room_y = pos[room]
            room_width, room_height = 0.15, 0.15

            rand_x = np.clip(room_x + np.random.uniform(-room_width / 2, room_width / 2), -1, 1)
            rand_y = np.clip(room_y + np.random.uniform(-room_height / 2, room_height / 2), -1, 1)

            img = Image.open(image_path)
            imagebox = OffsetImage(np.array(img), zoom=0.05)  # Convert PIL Image to numpy array
            ab = AnnotationBbox(imagebox, (rand_x, rand_y), frameon=False, pad=0)
            plt.gca().add_artist(ab)
        except Exception as e:
            print(f"Error loading image for {character}: {e}")

    # Plot the imposter inside its initial room
    imposter_image_path = character_images.get('I', 'path/to/default_character.png')
    try:
        imposter_room_x, imposter_room_y = pos[imposter_position]
        imposter_room_width, imposter_room_height = 0.15, 0.15

        imposter_rand_x = np.clip(
            imposter_room_x + np.random.uniform(-imposter_room_width / 2, imposter_room_width / 2), -1, 1)
        imposter_rand_y = np.clip(
            imposter_room_y + np.random.uniform(-imposter_room_height / 2, imposter_room_height / 2), -1, 1)

        imposter_img = Image.open(imposter_image_path)
        imposter_imagebox = OffsetImage(np.array(imposter_img), zoom=0.05)  # Convert PIL Image to numpy array
        imposter_ab = AnnotationBbox(imposter_imagebox, (imposter_rand_x, imposter_rand_y), frameon=False, pad=0)
        plt.gca().add_artist(imposter_ab)
    except Exception as e:
        print(f"Error loading image for imposter: {e}")


    # Plot small circles representing tasks inside the rooms
    light_green = (144 / 255, 238 / 255, 144 / 255) 
    for task, (task_x, task_y) in task_positions.items():
        if task in set().union(*tasks_completed.values()):
            plt.scatter(task_x, task_y, color=light_green, s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)
        else:
            plt.scatter(task_x, task_y, color='yellow', s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)

    # Remove completed tasks
    #remove_completed_tasks()

    # Check if the game has ended
    if game_ended():
        print("The game has ended.")
        
        if all_tasks_completed():
            print("\nCrewmates Win! All tasks completed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Crewmates Win! All tasks completed.', fontsize=20, ha='center', va='center', fontweight='bold')
        elif all_crewmates_killed():
            print("\nImposter Wins! All crewmates killed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Imposter Wins! All crewmates killed.', fontsize=20, ha='center', va='center', fontweight='bold')
        return

    # Plot task counter
    remaining_tasks = sum(len(tasks_in_room) for tasks_in_room in tasks.values()) - len(set().union(*tasks_completed.values()))
    plt.text(-1.1, 1.0, f'Remaining Tasks: {remaining_tasks}', fontsize=12, ha='left', va='center', fontweight='bold')

    plt.title(f'Among Us Map with Tasks - Frame {frame + 1}')
    plt.axis('off')

plt.figure(figsize=(15, 10))

animation = FuncAnimation(plt.gcf(), update, frames=100, interval=500, repeat=False)

animation.save('animation0.mp4', writer='ffmpeg', fps=2, dpi=300)

plt.show()

In [ ]:
# game where any crewmate can do any task

In [ ]:
#just playing around, tried to add more images

In [ ]:
room_layout = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"],
    # Include tasks and their corresponding rooms
    "T1": ["Reactor"],
    "T2": ["Medbay"],
    "T3": ["Electrical"],
    "T4": ["Cafeteria"],
    "T5": ["Storage"],
    "T6": ["Admin"],
    "T7": ["Security"],
    "T8": ["Oxygen"],
    "T9": ["Upper Engine"],
    "T10": ["Lower Engine"],
    "T11": ["Reactor"],
    "T12": ["Medbay"],
    "T13": ["Electrical"],
    "T14": ["Cafeteria"],
    "T15": ["Storage"],
    "T16": ["Admin"],
}

rooms = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"]
}

# Initialize the positions of crewmates, imposter, and tasks
crewmates = ['C1', 'C2', 'C3', 'C4', 'C5', 'C6']
imposter = 'I'
tasks = ['T1', 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T10',
         'T11', 'T12', 'T13', 'T14', 'T15', 'T16']

# Define different sizes for each room
room_sizes = {
    'Reactor': 9000,
    'Medbay': 7000,
    'Electrical': 8000,
    'Cafeteria': 6000,
    'Storage': 7000,
    'Admin': 9000,
    'Security': 6000,
    'Oxygen': 6000,
    'Upper Engine': 8000,
    'Lower Engine': 8000
}

tasks = {
    'Admin': ['T16', 'T6'],
    'Cafeteria': ['T14', 'T4'],
    'Medbay': ['T12', 'T2'],
    'Security': ['T7'],
    'Storage': ['T15', 'T5'],
    'Lower Engine': ['T10'],
    'Electrical' : ['T3', 'T13'],
    'Reactor' : ['T11', 'T1'],
    'Oxygen' : ['T8'],
    'Upper Engine' : ['T9'],
    
}

character_images = {
    'C1': 'crewmate1.png',
    'C2': 'crewmate2.png',
    'C3': 'crewmate3.png',
    'C4': 'crewmate4.png',
    'C5': 'crewmate5.png',
    'C6': 'crewmate6.png',
    'I': 'imposter.png'
}

# Ensure the number of tasks is less than or equal to the number of crewmates
num_crewmates = len(crewmates)
num_tasks = len(tasks)

# Assign random positions to crewmates, imposter, and tasks
crewmates_positions = dict(zip(crewmates, random.sample(list(rooms.keys()), len(crewmates))))
imposter_position = random.choice(list(rooms.keys()))

# Assign tasks to crewmates ensuring an equal split
tasks_per_crewmate = num_tasks // num_crewmates
tasks_assigned = {crewmate: [] for crewmate in crewmates}

# Assign tasks to rooms without ensuring uniqueness
tasks_positions = {task: random.choice(list(room_layout.keys())) for task in tasks}

for _ in range(tasks_per_crewmate):
    for crewmate in crewmates:
        available_tasks = set(tasks) - set(sum(tasks_assigned.values(), []))
        task = random.choice(list(available_tasks))
        tasks_assigned[crewmate].append(task)

        
# Print the corrected initial setup
print("Initial Setup:")
print("Rooms:", list(rooms.keys()))
print("Crewmates Positions:", crewmates_positions)
print("Imposter Position:", imposter_position)
print("Tasks Assigned:", tasks_assigned)
print("Tasks Positions:", tasks_positions)


# Function to handle crewmate movement
def crewmate_move(crewmate):
    current_room = crewmates_positions[crewmate]
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    crewmates_positions[crewmate] = new_room
    print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle imposter movement
def imposter_move():
    global imposter_position
    current_room = imposter_position
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    imposter_position = new_room
    print(f"The imposter moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
                
                # Remove completed task from the tasks dictionary
                if task in tasks:
                    tasks[current_room].remove(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a dictionary to track completed tasks for each crewmate
tasks_completed = {crewmate: set() for crewmate in crewmates}
print("tasks completed:", tasks_completed)



def delegate_uncompleted_tasks(killed_crewmate):
    uncompleted_tasks = set(tasks_assigned[killed_crewmate]) - set(tasks_completed[killed_crewmate])
    
    # Shuffle the uncompleted tasks to distribute them randomly
    uncompleted_tasks = list(uncompleted_tasks)
    random.shuffle(uncompleted_tasks)

    tasks_per_crewmate = len(uncompleted_tasks) // (num_crewmates - 1)
    
    # Distribute tasks equally among remaining crewmates
    for i, crewmate in enumerate(crewmates):
        if crewmate != killed_crewmate and crewmate not in crewmates_killed:
            start = i * tasks_per_crewmate
            end = (i + 1) * tasks_per_crewmate if i != num_crewmates - 2 else None
            tasks_assigned[crewmate].extend(uncompleted_tasks[start:end])
            
    
    tasks_assigned[killed_crewmate] = []
    




# Function to check crewmate death
def check_crewmate_death():
    global imposter_position
    for crewmate, position in crewmates_positions.items():
        if position == imposter_position and crewmate not in crewmates_killed:
            print(f"{crewmate} has been killed by the imposter!")
            crewmates_killed.add(crewmate)
            delegate_uncompleted_tasks(crewmate)

            # Remove killed crewmate from the list
            crewmates.remove(crewmate)

            # Update the character image for the killed crewmate
            character_images[crewmate] = f'deadcrewmate{crewmate[1]}.png'

            return True
    return False

def all_crewmates_killed():
    return len(crewmates) == 0

# Function to handle crewmate movement
def crewmate_move(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        adjacent_rooms = rooms[current_room]
        new_room = random.choice(adjacent_rooms)
        crewmates_positions[crewmate] = new_room
        print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a set to track killed crewmates
crewmates_killed = set()


    
def game_ended():
    return all_tasks_completed() or all_crewmates_killed()
    

# Function to check if all tasks are completed
def all_tasks_completed():
    completed_tasks_union = set().union(*tasks_completed.values())
    return completed_tasks_union == set(tasks)

# Function to check if all crewmates are killed
def all_crewmates_killed():
    return len(crewmates_killed) == num_crewmates
   

task_positions = {}
for room, tasks_in_room in rooms.items():
    for task_index, task in enumerate(tasks_in_room):
        task_x = pos[room][0] + np.random.uniform(-0.1, 0.1)
        task_y = pos[room][1] + np.random.uniform(-0.1, 0.1)
        task_positions[task] = (task_x, task_y)
    
game_outcome = None
# Function to update the animation frame
def update(frame):
    global game_outcome
    plt.clf()

    # Crewmates' movement and task assignment
    for crewmate in crewmates:
        crewmate_move(crewmate)
        crewmate_task(crewmate)
    print(crewmates)

    # Imposter's movement
    imposter_move()

    # Check crewmate death
    if check_crewmate_death():
        if all_crewmates_killed():
            print("All crewmates have been killed. Imposter wins!")
        return

    # Draw edges
    nx.draw_networkx_edges(G, pos, width=1, alpha=0.5, edge_color='gray')

    # Draw nodes
    nx.draw_networkx_nodes(
        G,
        pos,
        node_color='white',
        node_size=[room_sizes[node] for node in G.nodes],
        node_shape='s',
        edgecolors=[room_colors[node] for node in G.nodes],
        linewidths=3,
    )

    # Add task labels on the top left, and room names next to the rooms
    for room, connections in rooms.items():
        tasks_in_room = tasks.get(room, [])
        tasks_text = '\n'.join(tasks_in_room)
        plt.text(pos[room][0], pos[room][1] - 0.2, room, fontsize=10, ha='center', va='center', fontweight='bold')

    # Plot Among Us characters inside the rooms
    for character, room in crewmates_positions.items():
        image_path = character_images.get(character, 'path/to/default_character.png')

        try:
            room_x, room_y = pos[room]
            room_width, room_height = 0.15, 0.15 

            rand_x = np.clip(room_x + np.random.uniform(-room_width / 2, room_width / 2), -1, 1)
            rand_y = np.clip(room_y + np.random.uniform(-room_height / 2, room_height / 2), -1, 1)

            img = Image.open(image_path)
            imagebox = OffsetImage(np.array(img), zoom=0.05)
            ab = AnnotationBbox(imagebox, (rand_x, rand_y), frameon=False, pad=0)
            plt.gca().add_artist(ab)
        except Exception as e:
            print(f"Error loading image for {character}: {e}")

    # Plot the imposter inside its initial room
    imposter_image_path = character_images.get('I', 'path/to/default_character.png')
    try:
        imposter_room_x, imposter_room_y = pos[imposter_position]
        imposter_room_width, imposter_room_height = 0.15, 0.15

        imposter_rand_x = np.clip(
            imposter_room_x + np.random.uniform(-imposter_room_width / 2, imposter_room_width / 2), -1, 1)
        imposter_rand_y = np.clip(
            imposter_room_y + np.random.uniform(-imposter_room_height / 2, imposter_room_height / 2), -1, 1)

        imposter_img = Image.open(imposter_image_path)
        imposter_imagebox = OffsetImage(np.array(imposter_img), zoom=0.05)
        imposter_ab = AnnotationBbox(imposter_imagebox, (imposter_rand_x, imposter_rand_y), frameon=False, pad=0)
        plt.gca().add_artist(imposter_ab)
    except Exception as e:
        print(f"Error loading image for imposter: {e}")

    if not game_ended():
        # Plot small circles representing tasks inside the rooms
        light_green = (144 / 255, 238 / 255, 144 / 255) 
        print("tasks completed: ", tasks_completed.values())
        for task, (task_x, task_y) in task_positions.items():
            if task in set().union(*tasks_completed.values()):
                plt.scatter(task_x, task_y, color=light_green, s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)
            else:
                plt.scatter(task_x, task_y, color='yellow', s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)

    # Remove completed tasks
    #remove_completed_tasks()

    # Check if the game has ended
    if game_ended():
        print("The game has ended.")
        
        if all_tasks_completed():
            game_outcome = 'crewmates'
            print("\nCrewmates Win! All tasks completed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Crewmates Win! All tasks completed.', fontsize=20, ha='center', va='center', fontweight='bold')

            crewmate_win_img = Image.open('crewmatewin.png')
            # Zoom out by 2x
            crewmate_win_imagebox = OffsetImage(np.array(crewmate_win_img), zoom=plt.rcParams['figure.figsize'][0] * 0.15)
            plt.gca().add_artist(AnnotationBbox(crewmate_win_imagebox, (0.5, 0.5), frameon=False, pad=0))


        elif all_crewmates_killed():
            game_outcome = 'imposter'
            print("\nImposter Wins! All crewmates killed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Imposter Wins! All crewmates killed.', fontsize=20, ha='center', va='center', fontweight='bold')
            imposter_win_img = Image.open('imposterwin.png')
            # Zoom out by 2x
            imposter_win_imagebox = OffsetImage(np.array(imposter_win_img), zoom=plt.rcParams['figure.figsize'][0] * 0.15)
            plt.gca().add_artist(AnnotationBbox(imposter_win_imagebox, (0.5, 0.5), frameon=False, pad=0))
        return

    # Plot task counter in the top left
    remaining_tasks = sum(len(tasks_in_room) for tasks_in_room in tasks.values()) - len(set().union(*tasks_completed.values()))
    plt.text(-1.1, 1.0, f'Remaining Tasks: {remaining_tasks}', fontsize=12, ha='left', va='center', fontweight='bold')

    plt.title(f'Among Us Map with Tasks - Frame {frame + 1}')
    plt.axis('off')
    
#     # Display crewmate win image if crewmates win
#     if game_outcome == 'crewmates':
#         crewmate_win_img = Image.open('crewmatewin.png')
#         crewmate_win_imagebox = OffsetImage(np.array(crewmate_win_img), zoom=1.5)
#         plt.gca().add_artist(AnnotationBbox(crewmate_win_imagebox, (0.5, 0.5), frameon=False, pad=0))

#     if game_outcome == 'imposter':
#         crewmate_win_img = Image.open('imposterwin.png')
#         crewmate_win_imagebox = OffsetImage(np.array(crewmate_win_img), zoom=1.5)
#         plt.gca().add_artist(AnnotationBbox(crewmate_win_imagebox, (0.5, 0.5), frameon=False, pad=0))

        
        
plt.figure(figsize=(15, 10))

animation = FuncAnimation(plt.gcf(), update, frames=100, interval=500, repeat=False)

animation.save('animation1.mp4', writer='ffmpeg', fps=2, dpi=300)

plt.show()

In [ ]:
## With just 4 crewmates (original)

In [ ]:
room_layout = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"],
    # Include tasks and their corresponding rooms
    "T1": ["Reactor"],
    "T2": ["Medbay"],
    "T3": ["Electrical"],
    "T4": ["Cafeteria"],
    "T5": ["Storage"],
    "T6": ["Admin"],
    "T7": ["Security"],
    "T8": ["Oxygen"],
    "T9": ["Upper Engine"],
    "T10": ["Lower Engine"],
    "T11": ["Reactor"],
    "T12": ["Medbay"],
    "T13": ["Electrical"],
    "T14": ["Cafeteria"],
    "T15": ["Storage"],
    "T16": ["Admin"],
}

rooms = {
    "Reactor": ["Security", "Upper Engine"],
    "Medbay": ["Upper Engine", "Cafeteria"],
    "Electrical": ["Upper Engine", "Lower Engine"],
    "Cafeteria": ["Medbay", "Storage"],
    "Storage": ["Cafeteria", "Admin", "Electrical"],
    "Admin": ["Storage", "Security", "Oxygen"],
    "Security": ["Reactor", "Admin"],
    "Oxygen": ["Admin", "Lower Engine"],
    "Upper Engine": ["Reactor", "Medbay", "Electrical"],
    "Lower Engine": ["Electrical", "Oxygen"]
}

# Initialize the positions of crewmates, imposter, and tasks
crewmates = ['C1', 'C2', 'C3', 'C4']
imposter = 'I'
tasks = ['T1', 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T10',
         'T11', 'T12', 'T13', 'T14', 'T15', 'T16']

# Define different sizes for each room
room_sizes = {
    'Reactor': 9000,
    'Medbay': 7000,
    'Electrical': 8000,
    'Cafeteria': 6000,
    'Storage': 7000,
    'Admin': 9000,
    'Security': 6000,
    'Oxygen': 6000,
    'Upper Engine': 8000,
    'Lower Engine': 8000
}

tasks = {
    'Admin': ['T16', 'T6'],
    'Cafeteria': ['T14', 'T4'],
    'Medbay': ['T12', 'T2'],
    'Security': ['T7'],
    'Storage': ['T15', 'T5'],
    'Lower Engine': ['T10'],
    'Electrical' : ['T3', 'T13'],
    'Reactor' : ['T11', 'T1'],
    'Oxygen' : ['T8'],
    'Upper Engine' : ['T9'],
    
}

character_images = {
    'C1': 'crewmate1.png',
    'C2': 'crewmate2.png',
    'C3': 'crewmate3.png',
    'C4': 'crewmate4.png',
    'I': 'imposter.png'
}

# Ensure the number of tasks is less than or equal to the number of crewmates
num_crewmates = len(crewmates)
num_tasks = len(tasks)

# Assign random positions to crewmates, imposter, and tasks
crewmates_positions = dict(zip(crewmates, random.sample(list(rooms.keys()), len(crewmates))))
imposter_position = random.choice(list(rooms.keys()))

# Assign tasks to crewmates ensuring an equal split
tasks_per_crewmate = num_tasks // num_crewmates
tasks_assigned = {crewmate: [] for crewmate in crewmates}

# Assign tasks to rooms without ensuring uniqueness
tasks_positions = {task: random.choice(list(room_layout.keys())) for task in tasks}

for _ in range(tasks_per_crewmate):
    for crewmate in crewmates:
        available_tasks = set(tasks) - set(sum(tasks_assigned.values(), []))
        task = random.choice(list(available_tasks))
        tasks_assigned[crewmate].append(task)

        
# Print the corrected initial setup
print("Initial Setup:")
print("Rooms:", list(rooms.keys()))
print("Crewmates Positions:", crewmates_positions)
print("Imposter Position:", imposter_position)
print("Tasks Assigned:", tasks_assigned)
print("Tasks Positions:", tasks_positions)


# Function to handle crewmate movement
def crewmate_move(crewmate):
    current_room = crewmates_positions[crewmate]
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    crewmates_positions[crewmate] = new_room
    print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle imposter movement
def imposter_move():
    global imposter_position
    current_room = imposter_position
    adjacent_rooms = rooms[current_room]
    new_room = random.choice(adjacent_rooms)
    imposter_position = new_room
    print(f"The imposter moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
                
                # Remove completed task from the tasks dictionary
                if task in tasks:
                    tasks[current_room].remove(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a dictionary to track completed tasks for each crewmate
tasks_completed = {crewmate: set() for crewmate in crewmates}
print("tasks completed:", tasks_completed)



def delegate_uncompleted_tasks(killed_crewmate):
    uncompleted_tasks = set(tasks_assigned[killed_crewmate]) - set(tasks_completed[killed_crewmate])
    
    # Shuffle the uncompleted tasks to distribute them randomly
    uncompleted_tasks = list(uncompleted_tasks)
    random.shuffle(uncompleted_tasks)

    tasks_per_crewmate = len(uncompleted_tasks) // (num_crewmates - 1)
    
    # Distribute tasks equally among remaining crewmates
    for i, crewmate in enumerate(crewmates):
        if crewmate != killed_crewmate and crewmate not in crewmates_killed:
            start = i * tasks_per_crewmate
            end = (i + 1) * tasks_per_crewmate if i != num_crewmates - 2 else None
            tasks_assigned[crewmate].extend(uncompleted_tasks[start:end])
            
    
    tasks_assigned[killed_crewmate] = []
    




# Function to check crewmate death
def check_crewmate_death():
    global imposter_position
    for crewmate, position in crewmates_positions.items():
        if position == imposter_position and crewmate not in crewmates_killed:
            print(f"{crewmate} has been killed by the imposter!")
            crewmates_killed.add(crewmate)
            delegate_uncompleted_tasks(crewmate)

            # Remove killed crewmate from the list
            crewmates.remove(crewmate)

            # Update the character image for the killed crewmate
            character_images[crewmate] = f'deadcrewmate{crewmate[1]}.png'

            return True
    return False

def all_crewmates_killed():
    return len(crewmates) == 0

# Function to handle crewmate movement
def crewmate_move(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        adjacent_rooms = rooms[current_room]
        new_room = random.choice(adjacent_rooms)
        crewmates_positions[crewmate] = new_room
        print(f"{crewmate} moved from {current_room} to {new_room}")

# Function to handle crewmate task assignment and completion
def crewmate_task(crewmate):
    if crewmate not in crewmates_killed:
        current_room = crewmates_positions[crewmate]
        available_tasks = set(tasks_assigned[crewmate]) - set(tasks_completed[crewmate])

        if available_tasks:
            valid_tasks = [task for task in available_tasks if current_room in room_layout[task]]
            if valid_tasks:
                task = random.choice(valid_tasks)
                print(f"{crewmate} is performing task {task} in {current_room}")
                tasks_completed[crewmate].add(task)
            else:
                print(f"{crewmate} is in {current_room}, but has no available tasks in this room.")
        else:
            print(f"{crewmate} attempted to perform a task but has no available tasks in {current_room}")

# Initialize a set to track killed crewmates
crewmates_killed = set()


    
def game_ended():
    return all_tasks_completed() or all_crewmates_killed()
    

# Function to check if all tasks are completed
def all_tasks_completed():
    completed_tasks_union = set().union(*tasks_completed.values())
    return completed_tasks_union == set(tasks)

# Function to check if all crewmates are killed
def all_crewmates_killed():
    return len(crewmates_killed) == num_crewmates
   

    

# Function to update the animation frame
def update(frame):
    plt.clf()

    # Crewmates' movement and task assignment
    for crewmate in crewmates:
        crewmate_move(crewmate)
        crewmate_task(crewmate)
    print(crewmates)

    # Imposter's movement
    imposter_move()

    # Check crewmate death
    if check_crewmate_death():
        if all_crewmates_killed():
            print("All crewmates have been killed. Imposter wins!")
        return

    # Draw edges
    nx.draw_networkx_edges(G, pos, width=1, alpha=0.5, edge_color='gray')

    # Draw nodes
    nx.draw_networkx_nodes(
        G,
        pos,
        node_color='white',
        node_size=[room_sizes[node] for node in G.nodes],
        node_shape='s',
        edgecolors=[room_colors[node] for node in G.nodes],
        linewidths=3,
    )

    # Add task labels on the top left, and room names next to the rooms
    for room, connections in rooms.items():
        tasks_in_room = tasks.get(room, [])  # Get the tasks for the current room
        tasks_text = '\n'.join(tasks_in_room)
        plt.text(pos[room][0], pos[room][1] - 0.2, room, fontsize=10, ha='center', va='center', fontweight='bold')

    # Plot Among Us characters inside the rooms
    for character, room in crewmates_positions.items():
        image_path = character_images.get(character, 'path/to/default_character.png')

        try:
            room_x, room_y = pos[room]
            room_width, room_height = 0.15, 0.15

            rand_x = np.clip(room_x + np.random.uniform(-room_width / 2, room_width / 2), -1, 1)
            rand_y = np.clip(room_y + np.random.uniform(-room_height / 2, room_height / 2), -1, 1)

            img = Image.open(image_path)
            imagebox = OffsetImage(np.array(img), zoom=0.05)  # Convert PIL Image to numpy array
            ab = AnnotationBbox(imagebox, (rand_x, rand_y), frameon=False, pad=0)
            plt.gca().add_artist(ab)
        except Exception as e:
            print(f"Error loading image for {character}: {e}")

    # Plot the imposter inside its initial room
    imposter_image_path = character_images.get('I', 'path/to/default_character.png')
    try:
        imposter_room_x, imposter_room_y = pos[imposter_position]
        imposter_room_width, imposter_room_height = 0.15, 0.15

        imposter_rand_x = np.clip(
            imposter_room_x + np.random.uniform(-imposter_room_width / 2, imposter_room_width / 2), -1, 1)
        imposter_rand_y = np.clip(
            imposter_room_y + np.random.uniform(-imposter_room_height / 2, imposter_room_height / 2), -1, 1)

        imposter_img = Image.open(imposter_image_path)
        imposter_imagebox = OffsetImage(np.array(imposter_img), zoom=0.05)  # Convert PIL Image to numpy array
        imposter_ab = AnnotationBbox(imposter_imagebox, (imposter_rand_x, imposter_rand_y), frameon=False, pad=0)
        plt.gca().add_artist(imposter_ab)
    except Exception as e:
        print(f"Error loading image for imposter: {e}")

    # Plot small circles representing tasks inside the rooms
    task_radius = 0.1  # Adjust the size of the circles
    for room, tasks_in_room in tasks.items():
        for task_index, task in enumerate(tasks_in_room):
            task_x = pos[room][0] + np.random.uniform(-0.1, 0.1)
            task_y = pos[room][1] + np.random.uniform(-0.1, 0.1)
            plt.scatter(task_x, task_y, color='yellow', s=50, marker='o', edgecolors='black', linewidths=1, zorder=5)

    # Remove completed tasks
    #remove_completed_tasks()

    # Check if the game has ended
    if game_ended():
        print("The game has ended.")
        
        if all_tasks_completed():
            print("\nCrewmates Win! All tasks completed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Crewmates Win! All tasks completed.', fontsize=20, ha='center', va='center', fontweight='bold')
        elif all_crewmates_killed():
            print("\nImposter Wins! All crewmates killed.")
            plt.text((plt.xlim()[0] + plt.xlim()[1]) / 2, plt.ylim()[0]+.1, f'Imposter Wins! All crewmates killed.', fontsize=20, ha='center', va='center', fontweight='bold')
        return

    # Plot task counter in the top left
    remaining_tasks = sum(len(tasks_in_room) for tasks_in_room in tasks.values()) - len(set().union(*tasks_completed.values()))
    plt.text(-1.1, 1.0, f'Remaining Tasks: {remaining_tasks}', fontsize=12, ha='left', va='center', fontweight='bold')

    plt.title(f'Among Us Map with Tasks - Frame {frame + 1}')
    plt.axis('off')

plt.figure(figsize=(15, 10))

animation = FuncAnimation(plt.gcf(), update, frames=100, interval=500, repeat=False)

animation.save('animation.mp4', writer='ffmpeg', fps=2, dpi=300)

plt.show()